# Box Office Revenue Prediction

## Imports

In [100]:
import pandas as pd
import numpy as np


import re # regex
import ast

from datetime import datetime
from datetime import date

def warn(*args, **kwargs):
    pass
import warnings
warnings.warn = warn

from sklearn import metrics
from sklearn import preprocessing
from sklearn.pipeline import Pipeline
from sklearn.metrics import f1_score
from sklearn.preprocessing import StandardScaler
from sklearn.impute import SimpleImputer
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import GaussianNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.pipeline import make_pipeline
from sklearn.model_selection import learning_curve, RandomizedSearchCV, train_test_split
from sklearn.neural_network import MLPClassifier

## Data Sources
1. IMDB:
    * No. of ratings (star)
    * Avg. star rating (out of 10)
    * No. of user ratings (text reviews)
    * No. of critic ratings (meta critic)
    * Countries (truncate to just first country) - √
    * Language (truncate to just first language) - √
    * No. of languages (to be created from previous column) - √
    * Production house (truncate to just first production house) - √
    * Duration (convert to minutes/numeric from string) - √
    * Genre (need to explode to one-hot columns for 23 genres) - √
    * MPAA rating 
        * TV- ratings - reclassify - √ 
        * Not Rated --> PG-13/Unrated --> PG - many from non-English fall under these categories - √  
       
    * **Gross:** 'Y' variable (need to remove movies with alphabet-only gross, convert INR (other currencies?) to USD and 3 INR 3-digit movies):
        * Adjust for inflation, based on year of release - √ 
    * Release date:
        * convert first to datetime and use as a feature (holiday - US - release/not) - √ 

    
&nbsp; 
2. Popularity Scores:
    * Average popularity score per movie

&nbsp; 

3. Sentiment Scores:
    * AFINN score - based on IMDB user reviews pre-release
    * AFINN score - based on IMDB user reviews post-release
    

&nbsp;    
4. YouTube:
    * View count
    * Like count
    * Dislike count
    * Comment count

## Reading Excel File(s)
#### !!!!!! IMPORTANT- manually removed the unnamed serial number column from the popularity score excel sheet I'm reading below!!!!! 
#### Check that it is removed in your excel sheet also

In [3]:
# read popularity scores xlsx with IMDB_ID as the indexing column (2nd column from the left, or 1st index) 
df_pop = pd.read_excel("Final_data_sheets_updated_popularity_scores.xlsx", index_col = 0)
df = pd.read_excel("Final_data_sheets_with_Features.xlsx", index_col = 0)

In [5]:
df_pop = df_pop['Average_popularity_score_per_movie']

In [6]:
df_pop.head(2)

IMDB_ID
433362     8.318333
1216492    6.195667
Name: Average_popularity_score_per_movie, dtype: float64

In [7]:
# inspect
df.head(3)

Name  num_ratings  \
IMDB_ID                                                                   
1690470  Gekijouban Poketto monsutâ: Daiamondo & Pâru -...         1251   
1508290                                          Kyatapirâ          952   
2057455                               Dalpaengee eui byeol          323   

         avg_rating                             main_cast_list  \
IMDB_ID                                                          
1690470         6.2  Ikue Ôtani|Sarah Natochenny|Wayne Grayson   
1508290         6.7   Shinobu Terajima|Keigo Kasuya|Emi Masuda   
2057455         7.3     Cho Young-Chan|Kim Soon-ho|Choi Jungah   

                                           main_cast_links         dir_list  \
IMDB_ID                                                                       
1690470  /name/nm0649026/|/name/nm2516299/|/name/nm0969...  Kunihiko Yuyama   
1508290  /name/nm0855429/|/name/nm2486225/|/name/nm3787...   Kôji Wakamatsu   
2057455  /name/nm9804862/|/name/nm9804863/|/name/nm9804...     Seung-jun Yi   

                         creator_list  \
IMDB_ID                                 
1690470  Satoshi Tajiri|Hideki Sonoda   
1508290  Hisako Kurosawa|Masao Adachi   
2057455                           NaN   

                                                genre motion_picture_rating  \
IMDB_ID                                                                       
1690470  [Animation, Action, Family, Fantasy, Sci-Fi]             Not Rated   
1508290                                  [Drama, War]             Not Rated   
2057455                          [Documentary, Drama]             Not Rated   

                     release_date  ...          Language  \
IMDB_ID                            ...                     
1690470      10 July 2010 (Japan)  ...  Japanese|English   
1508290    14 August 2010 (Japan)  ...          Japanese   
2057455  15 February 2014 (Japan)  ...            Korean   

                                          Production_House  viewCount  \
IMDB_ID                                                                 
1690470   East Japan Marketing & Communications Inc., G...          0   
1508290                 Skhole Co., Wakamatsu Production            0   
2057455                    CreativeEAST, Dalpaengee, NHK            0   

         likeCount dislikeCount commentCount Afinn Pre Release  \
IMDB_ID                                                          
1690470          0            0            0               0.0   
1508290          0            0            0               0.0   
2057455          0            0            0               0.0   

        Afinn Post Release Release date  Holiday  
IMDB_ID                                           
1690470                0.0    2010-07-10       0  
1508290              -23.0    2010-08-14       0  
2057455               13.0    2014-02-15       0  

[3 rows x 28 columns]

In [8]:
list(df)

['Name',
 'num_ratings',
 'avg_rating',
 'main_cast_list',
 'main_cast_links',
 'dir_list',
 'creator_list',
 'genre',
 'motion_picture_rating',
 'release_date',
 'duration',
 'meta_critic_score',
 'num_user_ratings',
 'num_critic_ratings',
 'story_line',
 'others',
 'Gross',
 'Country',
 'Language',
 'Production_House',
 'viewCount',
 'likeCount',
 'dislikeCount',
 'commentCount',
 'Afinn Pre Release',
 'Afinn Post Release',
 'Release date ',
 'Holiday']

In [9]:
df = df.drop(['main_cast_list', 'main_cast_links','dir_list','creator_list', 'meta_critic_score','story_line', 'others', 'release_date'], axis = 1)

In [10]:
df.head(3)

Name  num_ratings  \
IMDB_ID                                                                   
1690470  Gekijouban Poketto monsutâ: Daiamondo & Pâru -...         1251   
1508290                                          Kyatapirâ          952   
2057455                               Dalpaengee eui byeol          323   

         avg_rating                                         genre  \
IMDB_ID                                                             
1690470         6.2  [Animation, Action, Family, Fantasy, Sci-Fi]   
1508290         6.7                                  [Drama, War]   
2057455         7.3                          [Documentary, Drama]   

        motion_picture_rating  duration  num_user_ratings  num_critic_ratings  \
IMDB_ID                                                                         
1690470             Not Rated  1h 36min               5.0                 3.0   
1508290             Not Rated  1h 25min               8.0                45.0   
2057455             Not Rated  1h 28min               4.0                33.0   

                Gross                    Country          Language  \
IMDB_ID                                                              
1690470   71,143,529                       Japan  Japanese|English   
1508290         2,109                      Japan          Japanese   
2057455         2,647  South Korea|Japan|Finland            Korean   

                                          Production_House  viewCount  \
IMDB_ID                                                                 
1690470   East Japan Marketing & Communications Inc., G...          0   
1508290                 Skhole Co., Wakamatsu Production            0   
2057455                    CreativeEAST, Dalpaengee, NHK            0   

         likeCount  dislikeCount  commentCount  Afinn Pre Release  \
IMDB_ID                                                             
1690470          0             0             0                0.0   
1508290          0             0             0                0.0   
2057455          0             0             0                0.0   

         Afinn Post Release Release date   Holiday  
IMDB_ID                                             
1690470                 0.0    2010-07-10        0  
1508290               -23.0    2010-08-14        0  
2057455                13.0    2014-02-15        0

In [11]:
# join df and df_pop
df = df.join(df_pop)

In [12]:
list(df)

['Name',
 'num_ratings',
 'avg_rating',
 'genre',
 'motion_picture_rating',
 'duration',
 'num_user_ratings',
 'num_critic_ratings',
 'Gross',
 'Country',
 'Language',
 'Production_House',
 'viewCount',
 'likeCount',
 'dislikeCount',
 'commentCount',
 'Afinn Pre Release',
 'Afinn Post Release',
 'Release date ',
 'Holiday',
 'Average_popularity_score_per_movie']

In [13]:
df.shape

(4351, 21)

## Data Transformations

### 1. Check for NAs/NANs

In [14]:
df.describe()

num_ratings   avg_rating  num_user_ratings  num_critic_ratings  \
count  4.351000e+03  4351.000000       4267.000000         4267.000000   
mean   4.943871e+04     6.466766        117.522615          132.775486   
std    1.108960e+05     0.960129        173.167208          140.513302   
min    9.000000e+00     1.500000          1.000000            1.000000   
25%    1.779500e+03     5.900000         13.000000           29.000000   
50%    8.299000e+03     6.600000         43.000000           77.000000   
75%    4.256200e+04     7.100000        145.000000          192.000000   
max    1.812301e+06     9.300000        998.000000          974.000000   

          viewCount     likeCount   dislikeCount   commentCount  \
count  4.351000e+03  4.351000e+03    4351.000000    4351.000000   
mean   1.588189e+06  1.064813e+04     844.473684    1067.971731   
std    6.871187e+06  7.684761e+04    7162.396242    9218.423397   
min    0.000000e+00  0.000000e+00       0.000000       0.000000   
25%    0.000000e+00  0.000000e+00       0.000000       0.000000   
50%    0.000000e+00  0.000000e+00       0.000000       0.000000   
75%    1.713150e+05  4.790000e+02      29.000000      46.500000   
max    2.224268e+08  3.483078e+06  244120.000000  476931.000000   

       Afinn Pre Release  Afinn Post Release      Holiday  \
count        4351.000000         4351.000000  4351.000000   
mean            8.816311           10.462413     0.033096   
std            12.745791           13.221700     0.178907   
min           -62.000000          -67.500000     0.000000   
25%             0.000000            0.000000     0.000000   
50%             5.000000            8.000000     0.000000   
75%            16.203297           18.125000     0.000000   
max           125.000000          106.000000     1.000000   

       Average_popularity_score_per_movie  
count                         4351.000000  
mean                             3.847854  
std                              3.476414  
min                              0.000000  
25%                              1.077167  
50%                              2.855333  
75%                              5.797000  
max                             21.596333

In [15]:
df.shape

(4351, 21)

#### Columns with NAs
MPAA rating, num_user_ratings, num_critic_ratings, language, production_house

In [16]:
df.isnull().any()

Name                                  False
num_ratings                           False
avg_rating                            False
genre                                 False
motion_picture_rating                  True
duration                               True
num_user_ratings                       True
num_critic_ratings                     True
Gross                                 False
Country                               False
Language                               True
Production_House                       True
viewCount                             False
likeCount                             False
dislikeCount                          False
commentCount                          False
Afinn Pre Release                     False
Afinn Post Release                    False
Release date                          False
Holiday                               False
Average_popularity_score_per_movie    False
dtype: bool

#### How many NAs total?
Could be multiple NAs for a given row.

In [17]:
df.isnull().sum().sum()

648

#### How many NAs per column?
Can it be manually fixed by finding the true value? Say, for duration of a couple of movies.

In [18]:
df.isnull().sum(axis = 0)

Name                                    0
num_ratings                             0
avg_rating                              0
genre                                   0
motion_picture_rating                 355
duration                                1
num_user_ratings                       84
num_critic_ratings                     84
Gross                                   0
Country                                 0
Language                               13
Production_House                      111
viewCount                               0
likeCount                               0
dislikeCount                            0
commentCount                            0
Afinn Pre Release                       0
Afinn Post Release                      0
Release date                            0
Holiday                                 0
Average_popularity_score_per_movie      0
dtype: int64

In [19]:
df[df['duration'].isnull()]

Name  num_ratings  avg_rating  \
IMDB_ID                                                            
3861006  Xiao shi dai 3: Ci jin shi dai          619         2.7   

                    genre motion_picture_rating duration  num_user_ratings  \
IMDB_ID                                                                      
3861006  [Drama, Romance]                   NaN      NaN               NaN   

         num_critic_ratings         Gross Country  ...  \
IMDB_ID                                            ...   
3861006                 NaN   86,900,000    China  ...   

                            Production_House viewCount  likeCount  \
IMDB_ID                                                             
3861006   Le Vision Pictures (Tianjin) Co.           0          0   

         dislikeCount  commentCount  Afinn Pre Release  Afinn Post Release  \
IMDB_ID                                                                      
3861006             0             0                0.0                 0.0   

         Release date  Holiday  Average_popularity_score_per_movie  
IMDB_ID                                                             
3861006     2014-07-17       0                            5.729333  

[1 rows x 21 columns]

This anyway has other columns as NaNs (info isn't available on IMDB anymore?),  so might as well drop the row.

#### If dropping all NAs?

In [20]:
# Lose 442 (45 rows still have NA in num_user_ratings, num_critic_ratings)
df = df.dropna(subset=['Language', 'Production_House','motion_picture_rating'])
df.shape

(3909, 21)

#### num_user_ratings and num_critic_ratings still have NAs - we will impute these later (pipelining) using median/mean

In [21]:
df.isnull().any()

Name                                  False
num_ratings                           False
avg_rating                            False
genre                                 False
motion_picture_rating                 False
duration                              False
num_user_ratings                       True
num_critic_ratings                     True
Gross                                 False
Country                               False
Language                              False
Production_House                      False
viewCount                             False
likeCount                             False
dislikeCount                          False
commentCount                          False
Afinn Pre Release                     False
Afinn Post Release                    False
Release date                          False
Holiday                               False
Average_popularity_score_per_movie    False
dtype: bool

In [22]:
# number of IMDB user reviews written
df['num_user_ratings'].isnull().sum()

42

In [23]:
# metacritic rating
df['num_critic_ratings'].isnull().sum()

42

### 2. Add number of languages

In [ ]:
# inspect unique values
df.Language.unique()

In [24]:
languages_split = df.Language.str.split(pat="|")
df['num_languages'] = languages_split.str.len()

In [ ]:
# inspect
df.head(3)

In [ ]:
# check NaN
df['num_languages'].isnull().values.any()

### 3. Truncate 'Languages' and 'Country'

In [ ]:
# inspect unique values
df.Country.unique()

In [25]:

languages_split = df.Language.str.split(pat="|").apply(lambda x: x[0])
df['Language'] = languages_split

In [26]:
countries_split = df.Country.str.split(pat="|").apply(lambda x: x[0])
df['Country'] = countries_split

In [ ]:
df.head(3)

In [ ]:
# check both columns for NaN
print(df['Language'].isnull().values.any())
print(df['Country'].isnull().values.any())

In [ ]:
# check how many unique values of each
print(len(df.Country.unique()))
print(len(df.Language.unique()))

### 4. Truncate 'Production_House'

In [ ]:
# inspect unique values - 3697 of them, can't see all
df.Production_House.unique()

In [27]:
production_house_split = df.Production_House.str.split(pat=", ").apply(lambda x: x[0])
df['Production_House'] = production_house_split

In [ ]:
# still could too unqiue of a column - 2277 unique values!
len(df.Production_House.unique())

### 5. Check MPAA column and regroup
https://simple.m.wikipedia.org/wiki/Motion_Picture_Association_of_America_film_rating_system

#### **Reclassification:**
* TV-Y, TV-7, TV-G --> G
* TV-PG --> PG
* TV-14 --> PG-13
* TV-MA --> R
* Not Rated (923!) --> 
* Unrated (143) -->

In [ ]:
# check NaN
df['motion_picture_rating'].isnull().values.any()

In [ ]:
# what are the unique ratings, and how many in each category?
df.groupby('motion_picture_rating').size()

In [28]:
df.loc[df['motion_picture_rating'].isin(["TV-G", "TV-Y7", "TV-Y"]), 'motion_picture_rating'] = "G"
df.loc[df['motion_picture_rating'].isin(["TV-PG"]), 'motion_picture_rating'] = "PG"
df.loc[df['motion_picture_rating'].isin(["TV-14", "M"]), 'motion_picture_rating'] = "PG-13"
df.loc[df['motion_picture_rating'].isin(["TV-MA"]), 'motion_picture_rating'] = "R"


df.loc[df['motion_picture_rating'].isin(["Unrated"]), 'motion_picture_rating'] = "PG" # mostly documentaries
df.loc[df['motion_picture_rating'].isin(["Not Rated"]), 'motion_picture_rating'] = "PG-13"

df.groupby('motion_picture_rating').size()

motion_picture_rating
G          45
NC-17       2
PG        520
PG-13    1888
R        1454
dtype: int64

In [ ]:
# check NaN after transforming
df['motion_picture_rating'].isnull().values.any()

### 6. Convert 'duration' column to time in minutes (integer)

In [29]:
def check_time(time):
    if len(time) == 1:
        if "h" in time[0]:
            new_time = 60*int(re.sub("\D", "", time[0]))
        else:
            new_time = int(re.sub("\D", "", time[0]))
    else:
        new_time = 60*int(re.sub("\D", "", time[0])) + int(re.sub("\D", "", time[1]))
    return new_time

test1 = df.duration.str.split(" ")
test2 = test1.apply(lambda x: check_time(x))

df['duration'] = test2

In [ ]:
# check unique values
print(df.duration.unique())

In [ ]:
## check for NaNs after transforming
df['duration'].isnull().values.any()

In [ ]:
list(df)

### 7. Expanding 'genre' to one-hot columns

In [ ]:
type(df['genre'].iloc[0]) # Need to convert string representation of list to an actual Python list to accumulate as et later

In [ ]:
# check unique genre lists
unique_genre_lists = df['genre'].unique()
print(unique_genre_lists) 

In [30]:
def convert_to_list(x):
    if "[" in x:
        x = re.sub("[\[\]]", "", x)
        x = x.split(", ")
    else:
        x = x.split(" ") # split by non-existent delimiter
    return x

In [31]:
# get all unique genres available
genre_lists = df.genre.apply(lambda x: convert_to_list(x))
df.genre = genre_lists

# temp = genre_lists.tolist()
# flattened =  [y for x in temp for y in x]
# print(set(flattened))

In [ ]:
type(df['genre'].iloc[0])

In [32]:
# add 23 new one-hot columns
from sklearn.preprocessing import MultiLabelBinarizer

mlb = MultiLabelBinarizer()
df = df.join(pd.DataFrame(mlb.fit_transform(df.pop('genre')),
                          columns=mlb.classes_,
                          index=df.index))

In [ ]:
df.head(3)

In [ ]:
list(df)

In [ ]:
# check for NaNs after transforming in all genre columns
df.shape

### 9. Cleaning up 'Gross'
Standardize currency, hard-code 3-digit movies, convert string to int/float

In [ ]:
type(df['Gross'].iloc[0])

In [44]:
pd.set_option('display.max_row', 4000)

In [ ]:
# look for values which have alphabetic characters in them => not in USD and  has to be converted
df[df.Gross.str.contains(pat = "[a-zA-Z]")]

In [33]:
# remove extra whitespaces, commas:
df['Gross'] = df.Gross.apply(lambda x: re.sub("[,\s]", "", x))
df[df.Gross.str.contains(pat = "[a-zA-Z]")]

Name  num_ratings  avg_rating  \
IMDB_ID                                                             
3417422                         Drishyam        23724         8.8   
6980546                  Bharat Ane Nenu        13039         8.0   
3569782                      Jigarthanda         8325         8.4   
5440700                            Theri        11077         7.2   
2106537       Matru ki Bijlee ka Mandola         5727         5.7   
6878378                          Vivegam         9840         5.9   
3848892                             Baby        47710         8.0   
3320578                           Veeram         6312         6.6   
6734984              Duvvada Jagannadham         2451         5.5   
4727512                      Srimanthudu         9548         7.6   
7098658                            Raazi        16995         7.8   
3495026                              Fan        38733         7.1   
5867800                            Aruvi         8034         8.8   
2877108                    Soodhu Kavvum         7153         8.4   
5457772                       Sarrainodu         3137         6.4   
5178278                          Vedalam         5139         6.3   
3142764                      Race Gurram         7531         7.2   
6485666                           Mersal        21747         8.0   
3563156                           Anjaan         3414         4.9   
5451690                   American Satan         2474         5.5   
5297256                      Pulimurugan         6133         7.0   
3802668         Govindudu Andari Vaadele         1607         5.7   
4258292                 Yennai Arindhaal         7193         7.3   
5098128                 Nannaku Prematho         7937         7.7   
6522546                           Spyder         7799         6.8   
6148156                     Vikram Vedha        17906         8.7   
5956100                  Tiger Zinda Hai        18396         6.1   
6027478                           Dhruva         4629         8.0   
2304655                     Gabbar Singh         5234         7.1   
1891755                          Billa 2         9798         6.3   
1512888                 Ayirathil Oruvan         2724         7.7   
1661031                     Brindaavanam         3195         7.2   
2082197                           Barfi!        68152         8.1   
1821478                         Kaavalan         4017         6.9   
2585562                            Pizza         5450         8.1   
2359810                       Raanjhanaa        26543         7.6   
1851988                               Ko         4481         7.8   
1375789                           Race 2        13933         5.3   
1965272                       Velayudham         9750         6.4   
3555036                           Legend         1554         6.5   
1655607                           Singam         4581         6.7   
1992138                            Force         6290         6.4   
1729637                        Bodyguard        20075         4.6   
2555958                         Arrambam         8017         7.2   
5460068                  Emo the Musical          795         6.2   
2204243                         Baadshah         3661         6.5   
403935                    Action Jackson         2812         3.3   
2309600                         Singam 2         4966         6.3   
1890493                      Oosaravelli         2946         6.6   
1753865                  Giochi d'estate          361         6.6   
2377938                  Special Chabbis        44672         8.0   
2362778  Saheb Biwi Aur Gangster Returns         3491         6.8   
3638644                       Seto Surya          362         7.0   

        motion_picture_rating  duration  num_user_ratings  num_critic_ratings  \
IMDB_ID                                                                         
3417422                 PG-13       160              81.0                10.0 

In [34]:
# add 7 trailing zeros for these 4:
# 6980546                 INR 206 Bharat Ane Nenu
# 3142764                 INR 130 Race Gurram
# 6734984                INR 157 Duvvada Jagannadham
# 6522546                INR 124 Spyder

gross_truncated = ["INR206", "INR130","INR157","INR124"]

df['Gross'] = df.Gross.apply(lambda x: x + "0000000" if x in gross_truncated else x)

In [35]:
# 1753865 Giochi d'estate - Gross not available on IMDB or elsewhere, drop the row
df.drop(1753865, inplace = True)

In [36]:
# for American Satan - VND 74 cumulative worldwide gross - change to USD $226,232
# https://www.the-numbers.com/movie/American-Satan#tab=international
df.at[5451690, 'Gross'] = "226232"

In [37]:
# Raazi - incorrectly entered as 2070 crores gross on IMDB, is actually ~207 crores
df.at[7098658, 'Gross'] = "2070000000"

In [38]:
from currency_converter import CurrencyConverter
c = CurrencyConverter()

def convert_currency(x):
    if re.search('[a-zA-Z£]', x) == None:
        return float(x)
    
    split_gross = re.split('(\d+)',x)
    
    # GBP
    if(split_gross[0] == "£"):
        return (c.convert(float(split_gross[1]), 'GBP','USD'))
    
    # NPR isn't supported CurrencyConverter - hard code
    if(split_gross[0]  == "NPR"):
        return (float(split_gross[1])*0.0090)
    
    return (c.convert(float(split_gross[1]), split_gross[0],'USD'))


df['Gross'] = df['Gross'].apply(lambda x : convert_currency(x))

In [ ]:
list(df)

In [ ]:
# check NaN
df['Gross'].isnull().values.any()

In [ ]:
df['Gross'].describe()

In [ ]:
type(df['Release date '].iloc[0])

In [39]:
#### Adjust gross for inflation based on the year - need inputs from Karthik for this:
def adjust_for_inflation(gross, release_date):
    if release_date.year == 2010:
        return(gross*1.152)
    elif release_date.year == 2011: 
        return(gross*1.124)
    elif release_date.year == 2012:
        return(gross*1.101)
    elif release_date.year == 2013:
        return(gross*1.087)
    elif release_date.year == 2014:
        return(gross*1.086)
    elif release_date.year == 2015:
        return(gross*1.068)
    elif release_date.year == 2016:
        return(gross*1.053)
    elif release_date.year == 2017:
        return(gross*1.032)
     # 2018 => just return x itself
    return gross
df['Gross'] = df.apply(lambda x: adjust_for_inflation(x['Gross'], x['Release date ']), axis=1)        

In [40]:
df['Gross'].describe()

count    3.908000e+03
mean     6.627972e+07
std      1.825128e+08
min      0.000000e+00
25%      8.093526e+04
50%      1.474008e+06
75%      3.683397e+07
max      2.208863e+09
Name: Gross, dtype: float64

### If dividing into equal revenue ranges (instead of quintiles)

In [ ]:
# def find_revenue_range(x):
#     if  0 <= x <= 588111000:
#         return 0
#     elif 588111001 <= x <= 1176222000:
#         return 1
#     elif 1176222000 <= x <= 1764333003:
#         return 2
#     elif 1764333003 <= x <= 2352444004:
#         return 3
#     else:
#         return 4
    
        
# df['gross_equal_range'] = df['Gross'].apply(lambda x: find_revenue_range(x))
 

In [ ]:
# df[df['gross_equal_range'] == 3]

## Categorize movies by gross revenue quintile
Split movies into 5 groups by revenue, and add (one-hot?) columns for classification.

In [ ]:
list(df.columns.values)

In [ ]:
df.head(5)

#### Divide into quintiles based on gross revenue
This divides into 5 balanced classes.
*** Dividing into 5 based on manually selected ranges results in a very high accuracy ~97%, because it is highly imbalanced - even easiest prediction of majority class can result in this accuracy.  **

In [41]:
ret_value = pd.qcut(df['Gross'], 5, labels=["very low", "low", "medium", "high", "very high"], retbins = True)

#### Check bucket values

In [42]:
df['gross_category'] = ret_value[0]
ret_value[1]
# very low ends at 4.869325e+04, 
#low ends at 3.891683e+05, medium ends at 5.904366e+06, 
# high ends at 6.748606e+07, very high ends at 2.208863e+09

array([0.00000000e+00, 4.88742888e+04, 3.90153180e+05, 5.90707620e+06,
       6.74920807e+07, 2.20886283e+09])

In [43]:
df.groupby('gross_category').size()

gross_category
very low     782
low          781
medium       782
high         781
very high    782
dtype: int64

In [45]:
df_sorted = df.sort_values(['Gross'])

#### This prints the whole dataframe (all ~3k rows)! 

In [46]:
df_sorted

Name  num_ratings  \
IMDB_ID                                                                   
1925479                                       Officer Down         4961   
4874206                                         (M)uchenik         3764   
4372390                                             Detour         4559   
1810697                                       Meeting Evil        11192   
4796122                                            Satanic         5188   
1682940                                           Playback         4474   
5038358                   Des nouvelles de la planète Mars          888   
2289920                                    Justice Is Mind           96   
1384927                               Death of a Superhero         3206   
4428762                                         Éperdument         1116   
1493157                                       Nature Calls         2095   
2275471                                      A Perfect Man         1792   
5143704                                      Green is Gold          824   
1503777                                            Illégal          824   
2193418                                 Hammer of the Gods         7488   
1682186                                           Headshot         1602   
1559040                                       Angels Crest         1759   
1657299                                    The Decoy Bride         9922   
762138                                               Syrup        10166   
3334212                                   This Isn't Funny          348   
1649443                               [REC] 4: Apocalipsis        14120   
4439102                                      Officer Downe         1576   
3324494              La prochaine fois je viserai le coeur         2172   
1830792                                             Romeos         3001   
3213222                                          Big Muddy          144   
3130776                                 She's Lost Control          712   
2385195                            Rhymes for Young Ghouls          966   
2385227                                            Sunrise          246   
850677                                        Jack & Diane         2521   
1612782                                 The Butterfly Room         1776   
1541160                                           Flypaper        30197   
1522296                                     Snowman's Land          643   
1641841                                         Skin Trade         6860   
2363213                                     Gåten Ragnarok         6894   
1487118                                        Chalet Girl        22173   
2123884                             3 Nights in the Desert         1404   
1865346                              Detention of the Dead         2396   
1656179                                 I Kissed a Vampire          355   
1436559                            Love, Wedding, Marriage         8623   
2125439                                          Bestiaire          355   
1884457                                        The Package         3606   
1480658                                              Eddie         1349   
4875456                     Best and Most Beautiful Things          139   
2574576                                          Cut Snake         1127   
2241750                                              Drown         1166   
2924352                                          Hayride 2          614   
1853643                                      Why Stop Now?         7018   
1747967                                          Cassadaga         3106   
2726552                                   A Kind of Murder         5740   
1867093                                      The Samaritan         9000   
1235841                                         Medianeras        12741   
1885300                                      Best Man Down         8774   
3240

## Classification Models
### Logistic Regression Classification

In [47]:
df_cleaned = df.copy()

In [48]:
df_cleaned.head(5)

Name  num_ratings  \
IMDB_ID                                                                   
1690470  Gekijouban Poketto monsutâ: Daiamondo & Pâru -...         1251   
1508290                                          Kyatapirâ          952   
2057455                               Dalpaengee eui byeol          323   
2077826  Gekijoban Poketto Monsuta besuto uisshu bikuti...         1152   
1937133                          De l'autre côté du périph         4319   

         avg_rating motion_picture_rating  duration  num_user_ratings  \
IMDB_ID                                                                 
1690470         6.2                 PG-13        96               5.0   
1508290         6.7                 PG-13        85               8.0   
2057455         7.3                 PG-13        88               4.0   
2077826         6.1                 PG-13        88               4.0   
1937133         5.8                     R        96               5.0   

         num_critic_ratings         Gross      Country  Language  ... Mystery  \
IMDB_ID                                                           ...           
1690470                 3.0  8.195735e+07        Japan  Japanese  ...       0   
1508290                45.0  2.429568e+03        Japan  Japanese  ...       0   
2057455                33.0  2.874642e+03  South Korea    Korean  ...       0   
2077826                 4.0  6.416072e+07        Japan  Japanese  ...       0   
1937133                36.0  6.521223e+03       France    French  ...       0   

         News  Romance  Sci-Fi  Short  Sport  Thriller War  Western  \
IMDB_ID                                                               
1690470     0        0       1      0      0         0   0        0   
1508290     0        0       0      0      0         0   1        0   
2057455     0        0       0      0      0         0   0        0   
2077826     0        0       1      0      0         0   0        0   
1937133     0        0       0      0      0         0   0        0   

         gross_category  
IMDB_ID                  
1690470       very high  
1508290        very low  
2057455        very low  
2077826            high  
1937133        very low  

[5 rows x 45 columns]

### Dealing with categorical features
Inspect non-numeric columns:

* Country                                 object -- 61 unique - categorize as top 5 vs. others 
* Language                                object -- 77 unique - categorize as top 5 vs. others 
* Production_House                        object -- ~2000+ unique - categorize as top 5 vs. othersCheck
* motion_picture_rating                   object -- only 5 groups 
* Name                                    object -- drop, too unique, unless using to derive a text-based feature
* release_date                            object -- drop, can be used to extract weekend/not later 

In [ ]:
df_cleaned.dtypes

#### Check production house split

In [ ]:
df_cleaned['Production_House'].dtypes

In [ ]:
df_cleaned['Production_House'].head(5)

In [ ]:
# could do top 5 vs others
df_cleaned.groupby('Production_House').size().sort_values(ascending = False).head(20)

In [49]:
top_production = list(df_cleaned.groupby('Production_House').size().sort_values(ascending = False).head(5).index)

df_cleaned['Production_House'] = df_cleaned.Production_House.apply(lambda x: x if x in top_production
                                         else "Other")

In [50]:
df_cleaned.groupby('Production_House').size().sort_values(ascending = False)

Production_House
Other                             3583
 Universal Pictures                 80
 Columbia Pictures Corporation      70
 Paramount Pictures                 63
 Warner Bros.                       61
 Twentieth Century Fox              51
dtype: int64

#### Check language split

In [ ]:
df_cleaned.groupby('Language').size().sort_values(ascending = False).head(20) # could do English, French, Hindi, Spanish, Mandarin vs. others

In [51]:
top_language = list(df_cleaned.groupby('Language').size().sort_values(ascending = False).head(5).index)

df_cleaned['Language'] = df_cleaned.Language.apply(lambda x: x if x in top_language
                                         else "Other")

In [52]:
df_cleaned.groupby('Language').size().sort_values(ascending = False)

Language
English     2961
Other        454
French       194
Hindi        151
Spanish       81
Mandarin      67
dtype: int64

#### Check country split

In [ ]:
df_cleaned.groupby('Country').size().sort_values(ascending = False).head(20) # could do USA, UK, France, India, Canada, China vs. others

In [53]:
top_countries = list(df_cleaned.groupby('Country').size().sort_values(ascending = False).head(5).index)

df_cleaned['Country'] = df_cleaned.Country.apply(lambda x: x if x in top_countries
                                         else "Other")

In [54]:
df_cleaned.groupby('Country').size().sort_values(ascending = False)

Country
USA       2211
Other      810
UK         352
France     237
India      198
Canada     100
dtype: int64

### One-Hot Encoding 
For categorical features, and the gross_category label.

In [56]:
X = df_cleaned.drop(['gross_category', 'Gross', 'Name', 'Release date '], axis=1) 
# drop is NOT in-place by default, doesn't affect original DF

y = df_cleaned['gross_category'].copy()

In [57]:
X.dtypes

num_ratings                             int64
avg_rating                            float64
motion_picture_rating                  object
duration                                int64
num_user_ratings                      float64
num_critic_ratings                    float64
Country                                object
Language                               object
Production_House                       object
viewCount                               int64
likeCount                               int64
dislikeCount                            int64
commentCount                            int64
Afinn Pre Release                     float64
Afinn Post Release                    float64
Holiday                                 int64
Average_popularity_score_per_movie    float64
num_languages                           int64
Action                                  int64
Adventure                               int64
Animation                               int64
Biography                         

In [58]:
X.shape 

(3908, 41)

In [59]:
#categorical_cols = ["motion_picture_rating", "Country", "Language",  "Production_House"]
X_dummies = pd.get_dummies(X)

In [60]:
X_dummies.shape # 41 -4 + 18 + 5 = 60

(3908, 60)

In [61]:
X_dummies.head(5)

num_ratings  avg_rating  duration  num_user_ratings  \
IMDB_ID                                                        
1690470         1251         6.2        96               5.0   
1508290          952         6.7        85               8.0   
2057455          323         7.3        88               4.0   
2077826         1152         6.1        88               4.0   
1937133         4319         5.8        96               5.0   

         num_critic_ratings  viewCount  likeCount  dislikeCount  commentCount  \
IMDB_ID                                                                         
1690470                 3.0          0          0             0             0   
1508290                45.0          0          0             0             0   
2057455                33.0          0          0             0             0   
2077826                 4.0          0          0             0             0   
1937133                36.0          0          0             0             0   

         Afinn Pre Release  ...  Language_Hindi  Language_Mandarin  \
IMDB_ID                     ...                                      
1690470                0.0  ...               0                  0   
1508290                0.0  ...               0                  0   
2057455                0.0  ...               0                  0   
2077826                0.0  ...               0                  0   
1937133                0.0  ...               0                  0   

         Language_Other  Language_Spanish  \
IMDB_ID                                     
1690470               1                 0   
1508290               1                 0   
2057455               1                 0   
2077826               1                 0   
1937133               0                 0   

         Production_House_ Columbia Pictures Corporation  \
IMDB_ID                                                    
1690470                                                0   
1508290                                                0   
2057455                                                0   
2077826                                                0   
1937133                                                0   

         Production_House_ Paramount Pictures  \
IMDB_ID                                         
1690470                                     0   
1508290                                     0   
2057455                                     0   
2077826                                     0   
1937133                                     0   

         Production_House_ Twentieth Century Fox  \
IMDB_ID                                            
1690470                                        0   
1508290                                        0   
2057455                                        0   
2077826                                        0   
1937133                                        0   

         Production_House_ Universal Pictures  Production_House_ Warner Bros.  \
IMDB_ID                                                                         
1690470                                     0                               0   
1508290                                     0                               0   
2057455                                     0                               0   
2077826                                     0                               0   
1937133                                     0                               0   

         Production_House_Other  
IMDB_ID                          
1690470                       1  
1508290                       1  
2057455                       1  
2077826                       1  
1937133                       1  

[5 rows x 60 columns]

In [62]:
le = preprocessing.LabelEncoder()
le.fit(y)

LabelEncoder()

In [63]:
list(le.classes_)

['high', 'low', 'medium', 'very high', 'very low']

In [64]:
y_encoded = le.transform(y) 

### Split data - train, test

In [65]:
X_train, X_test, y_train, y_test = train_test_split(X_dummies, y_encoded, random_state=1)

In [66]:
X_train.shape

(2931, 60)

In [67]:
X_test.shape

(977, 60)

In [68]:
imputer = SimpleImputer()
scaler = StandardScaler()
lr = LogisticRegression(multi_class = "multinomial", solver = 'newton-cg', max_iter = 5000)

pipe = Pipeline([('imputer', imputer),
                 ('scaler', scaler), 
                 ('lr', lr)])


pipe.fit(X_train, y_train) 

Pipeline(memory=None,
     steps=[('imputer', SimpleImputer(copy=True, fill_value=None, missing_values=nan, strategy='mean',
       verbose=0)), ('scaler', StandardScaler(copy=True, with_mean=True, with_std=True)), ('lr', LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=5000, multi_class='multinomial',
          n_jobs=None, penalty='l2', random_state=None, solver='newton-cg',
          tol=0.0001, verbose=0, warm_start=False))])

In [ ]:
pipe.named_steps.keys()

In [ ]:
# for any continuous parameters, specify a distribution instead of a list of options
param_grid = {}
param_grid['imputer__strategy'] = ["mean", "median"]
param_grid['scaler__with_mean'] = [True, False]
param_grid['scaler__with_std'] = [True, False]
param_grid['lr__C'] = [1, 0.75, 0.5] # smaller specifies stronger regularization
param_grid

In [ ]:
# additional parameters are n_iter (number of searches) and random_state
rand = RandomizedSearchCV(pipe, param_grid, cv=5, scoring='accuracy', n_iter=5, random_state=1)

In [ ]:
# time the randomized search
%time rand.fit(X_train, y_train)

In [ ]:
print(rand.best_score_) # hold-out set
print(rand.best_params_)
# print the best model found by RandomizedSearchCV
print(rand.best_estimator_)

In [ ]:
# predictions on train and test data with best estimator
y_trainpred0 = rand.predict(X_train)
y_pred0 = rand.predict(X_test)

print(metrics.accuracy_score(y_test, y_pred0))
print(metrics.f1_score(y_test, y_pred0, average='macro')) 

In [ ]:
# train set
print(metrics.accuracy_score(y_train, y_trainpred0))
print(metrics.f1_score(y_train, y_trainpred0, average='macro'))

In [ ]:
# interpretation 
lr.coef_

In [ ]:
lr.coef_.shape

### k-NN Classification

In [69]:
knn = KNeighborsClassifier()
pipe_knn = Pipeline([('imputer', imputer),
                 ('scaler', scaler), 
                 ('knn', knn)])
# pipeline steps are automatically assigned names by make_pipeline

In [70]:
param_grid = {}
param_grid['imputer__strategy'] = ["mean", "median"]
param_grid['scaler__with_mean'] = [True, False]
param_grid['scaler__with_std'] = [True, False]
param_grid['knn__n_neighbors'] = [50, 100, 150, 200, 250] 
param_grid['knn__weights'] = ['uniform', 'distance'] 
param_grid['knn__algorithm'] = ['auto', 'ball_tree', 'kd_tree', 'brute']
param_grid

{'imputer__strategy': ['mean', 'median'],
 'scaler__with_mean': [True, False],
 'scaler__with_std': [True, False],
 'knn__n_neighbors': [50, 100, 150, 200, 250],
 'knn__weights': ['uniform', 'distance'],
 'knn__algorithm': ['auto', 'ball_tree', 'kd_tree', 'brute']}

In [71]:
rand_knn = RandomizedSearchCV(pipe_knn, param_grid, cv=5, scoring='accuracy', n_iter=5, random_state=1)

In [72]:
# time the randomized search
%time rand_knn.fit(X_train, y_train)

CPU times: user 19.1 s, sys: 1.3 s, total: 20.4 s
Wall time: 13.5 s


RandomizedSearchCV(cv=5, error_score='raise-deprecating',
          estimator=Pipeline(memory=None,
     steps=[('imputer', SimpleImputer(copy=True, fill_value=None, missing_values=nan, strategy='mean',
       verbose=0)), ('scaler', StandardScaler(copy=True, with_mean=True, with_std=True)), ('knn', KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
           metric_params=None, n_jobs=None, n_neighbors=5, p=2,
           weights='uniform'))]),
          fit_params=None, iid='warn', n_iter=5, n_jobs=None,
          param_distributions={'imputer__strategy': ['mean', 'median'], 'scaler__with_mean': [True, False], 'scaler__with_std': [True, False], 'knn__n_neighbors': [50, 100, 150, 200, 250], 'knn__weights': ['uniform', 'distance'], 'knn__algorithm': ['auto', 'ball_tree', 'kd_tree', 'brute']},
          pre_dispatch='2*n_jobs', random_state=1, refit=True,
          return_train_score='warn', scoring='accuracy', verbose=0)

In [73]:
print(rand_knn.best_score_) # hold-out set
print(rand_knn.best_params_)

0.4612760150119413
{'scaler__with_std': True, 'scaler__with_mean': True, 'knn__weights': 'uniform', 'knn__n_neighbors': 50, 'knn__algorithm': 'kd_tree', 'imputer__strategy': 'mean'}


In [74]:
# print the best model found by RandomizedSearchCV
print(rand_knn.best_estimator_)

Pipeline(memory=None,
     steps=[('imputer', SimpleImputer(copy=True, fill_value=None, missing_values=nan, strategy='mean',
       verbose=0)), ('scaler', StandardScaler(copy=True, with_mean=True, with_std=True)), ('knn', KNeighborsClassifier(algorithm='kd_tree', leaf_size=30, metric='minkowski',
           metric_params=None, n_jobs=None, n_neighbors=50, p=2,
           weights='uniform'))])


In [75]:
# predictions on train and test data with best estimator
y_trainpred_knn = rand_knn.predict(X_train)
y_pred_knn = rand_knn.predict(X_test)

print(metrics.accuracy_score(y_test, y_pred_knn))
print(metrics.f1_score(y_test, y_pred_knn, average='macro'))

0.4749232343909928
0.47823249337774687


In [76]:
# train set
print(metrics.accuracy_score(y_train, y_trainpred_knn))
print(metrics.f1_score(y_train, y_trainpred_knn, average='macro'))

0.49334698055271237
0.4919488072117538


### Random Forest Classification

In [77]:
rf = RandomForestClassifier(random_state=0)
pipe_rf = Pipeline([('imputer', imputer),
                 ('scaler', scaler), 
                 ('rf', rf)])


In [78]:
param_grid = {}
param_grid['imputer__strategy'] = ["mean", "median"]
param_grid['scaler__with_mean'] = [True, False]
param_grid['scaler__with_std'] = [True, False]
param_grid['rf__n_estimators'] = [50, 100, 150, 200, 300, 500, 600]  # how many trees to use in the forest
param_grid['rf__max_depth'] = [3, 5, 7, 9] # max depth
param_grid['rf__criterion'] = ['gini', 'entropy']
param_grid['rf__max_features'] = ['auto', 'log2'] # like mtry
param_grid['rf__oob_score'] = [True, False] 
param_grid

{'imputer__strategy': ['mean', 'median'],
 'scaler__with_mean': [True, False],
 'scaler__with_std': [True, False],
 'rf__n_estimators': [50, 100, 150, 200, 300, 500, 600],
 'rf__max_depth': [3, 5, 7, 9],
 'rf__criterion': ['gini', 'entropy'],
 'rf__max_features': ['auto', 'log2'],
 'rf__oob_score': [True, False]}

In [79]:
rand_rf = RandomizedSearchCV(pipe_rf, param_grid, cv=5, scoring='accuracy', n_iter=5, random_state=1)

In [80]:
# time the randomized search
%time rand_rf.fit(X_train, y_train)

CPU times: user 29.4 s, sys: 332 ms, total: 29.8 s
Wall time: 31.6 s


RandomizedSearchCV(cv=5, error_score='raise-deprecating',
          estimator=Pipeline(memory=None,
     steps=[('imputer', SimpleImputer(copy=True, fill_value=None, missing_values=nan, strategy='mean',
       verbose=0)), ('scaler', StandardScaler(copy=True, with_mean=True, with_std=True)), ('rf', RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, m...ors='warn', n_jobs=None,
            oob_score=False, random_state=0, verbose=0, warm_start=False))]),
          fit_params=None, iid='warn', n_iter=5, n_jobs=None,
          param_distributions={'imputer__strategy': ['mean', 'median'], 'scaler__with_mean': [True, False], 'scaler__with_std': [True, False], 'rf__n_estimators': [50, 100, 150, 200, 300, 500, 600], 'rf__max_depth': [3, 5, 7, 9], 'rf__criterion': ['gini', 'entropy'], 'rf__max_features': ['auto', 'log2'], 'rf__oob_score': [True, False]},
          pre_dispatch='2*n_jobs', random_state=1, refit=True,
          return_train_sc

In [81]:
print(rand_rf.best_score_) # hold-out set
print(rand_rf.best_params_)

0.5554418287273968
{'scaler__with_std': False, 'scaler__with_mean': False, 'rf__oob_score': False, 'rf__n_estimators': 600, 'rf__max_features': 'log2', 'rf__max_depth': 9, 'rf__criterion': 'entropy', 'imputer__strategy': 'median'}


In [85]:
# print the best model found by RandomizedSearchCV
print(rand_rf.best_estimator_)

Pipeline(memory=None,
     steps=[('imputer', SimpleImputer(copy=True, fill_value=None, missing_values=nan,
       strategy='median', verbose=0)), ('scaler', StandardScaler(copy=True, with_mean=False, with_std=False)), ('rf', RandomForestClassifier(bootstrap=True, class_weight=None, criterion='entropy',
            max_depth=...mators=600, n_jobs=None,
            oob_score=False, random_state=0, verbose=0, warm_start=False))])


In [83]:
# predictions on train and test data with best estimator
y_trainpred_rf = rand_rf.predict(X_train)
y_pred_rf = rand_rf.predict(X_test)

print(metrics.accuracy_score(y_test, y_pred_rf))
print(metrics.f1_score(y_test, y_pred_rf, average='macro'))

0.5537359263050153
0.54475542632895


In [84]:
# train set
print(metrics.accuracy_score(y_train, y_trainpred_rf))
print(metrics.f1_score(y_train, y_trainpred_rf, average='macro'))

0.8065506653019447
0.8038368493078718


In [ ]:
rf.feature_importances #cannot do this when using pipeline?

### Naive Bayes Classificiation

In [92]:
nb = GaussianNB()
pipe_nb = Pipeline([('imputer', imputer),
                 ('scaler', scaler), 
                 ('nb', nb)])



In [97]:
param_grid = {}
param_grid['imputer__strategy'] = ["mean", "median"]
param_grid['scaler__with_mean'] = [True, False]
param_grid['scaler__with_std'] = [True, False]
param_grid

{'imputer__strategy': ['mean', 'median'],
 'scaler__with_mean': [True, False],
 'scaler__with_std': [True, False]}

In [98]:
rand_nb = RandomizedSearchCV(pipe_nb, param_grid, cv=5, scoring='accuracy', n_iter=5, random_state=1)

In [99]:
# time the randomized search
%time rand_nb.fit(X_train, y_train)

ValueError: Input X must be non-negative

In [ ]:
print(rand_nb.best_score_) # hold-out set
print(rand_nb.best_params_)

In [ ]:
# print the best model found by RandomizedSearchCV
print(rand_nb.best_estimator_)

In [ ]:
# predictions on train and test data with best estimator
y_trainpred_nb = rand_nb.predict(X_train)
y_pred_nb = rand_nb.predict(X_test)

print(metrics.accuracy_score(y_test, y_pred_nb))
print(metrics.f1_score(y_test, y_pred_nb, average='macro'))

In [ ]:
# train set
print(metrics.accuracy_score(y_train, y_trainpred_nb))
print(metrics.f1_score(y_train, y_trainpred_nb, average='macro'))

### MLP Classification

In [103]:
mlp = MLPClassifier(random_state=0)
pipe_mlp = Pipeline([('imputer', imputer),
                 ('scaler', scaler), 
                 ('mlp', mlp)])



In [105]:
param_grid = {}
param_grid['imputer__strategy'] = ["mean", "median"]
param_grid['scaler__with_mean'] = [True, False]
param_grid['scaler__with_std'] = [True, False]
# param_grid['mlp__n_estimators'] = [50, 100, 150, 200, 300, 500, 600]  # how many trees to use in the forest
# param_grid['mlp__max_depth'] = [3, 5, 7, 9] # max depth
# param_grid['mlp__criterion'] = ['gini', 'entropy']
# param_grid['mlp__max_features'] = ['auto', 'log2'] # like mtry
# param_grid['mlp__oob_score'] = [True, False] 
param_grid

{'imputer__strategy': ['mean', 'median'],
 'scaler__with_mean': [True, False],
 'scaler__with_std': [True, False]}

In [106]:
rand_mlp = RandomizedSearchCV(pipe_mlp, param_grid, cv=5, scoring='accuracy', n_iter=5, random_state=1)

In [107]:
# time the randomized search
%time rand_mlp.fit(X_train, y_train)

CPU times: user 1min 41s, sys: 1.68 s, total: 1min 43s
Wall time: 57.6 s


RandomizedSearchCV(cv=5, error_score='raise-deprecating',
          estimator=Pipeline(memory=None,
     steps=[('imputer', SimpleImputer(copy=True, fill_value=None, missing_values=nan, strategy='mean',
       verbose=0)), ('scaler', StandardScaler(copy=True, with_mean=True, with_std=True)), ('mlp', MLPClassifier(activation='relu', alpha=0.0001, batch_size='auto', beta_1=0.9,
       beta_2=0.999, early...=True, solver='adam', tol=0.0001,
       validation_fraction=0.1, verbose=False, warm_start=False))]),
          fit_params=None, iid='warn', n_iter=5, n_jobs=None,
          param_distributions={'imputer__strategy': ['mean', 'median'], 'scaler__with_mean': [True, False], 'scaler__with_std': [True, False]},
          pre_dispatch='2*n_jobs', random_state=1, refit=True,
          return_train_score='warn', scoring='accuracy', verbose=0)

In [ ]:
print(rand_mlp.best_score_) # hold-out set
print(rand_mlp.best_params_)

In [ ]:
# print the best model found by RandomizedSearchCV
print(rand_mlp.best_estimator_)

In [ ]:
# predictions on train and test data with best estimator
y_trainpred_mlp = rand_mlp.predict(X_train)
y_pred_mlp = rand_nb.predict(X_test)

print(metrics.accuracy_score(y_test, y_pred_mlp))
print(metrics.f1_score(y_test, y_pred_mlp, average='macro'))

In [ ]:
# train set
print(metrics.accuracy_score(y_train, y_trainpred_mlp))
print(metrics.f1_score(y_train, y_trainpred_mlp, average='macro'))

## Further evaluation of best-performing model

In [ ]:
# classification report 
from sklearn.metrics import classification_report
print(classification_report(y_test, y_pred_rf, target_names=["very low", "low", "medium", "high", "very high"]))

In [ ]:
# confusion matrix
# from https://scikit-learn.org/stable/auto_examples/model_selection/plot_confusion_matrix.html#sphx-glr-auto-examples-model-selection-plot-confusion-matrix-py
import numpy as np
import matplotlib.pyplot as plt

from sklearn.metrics import confusion_matrix
from sklearn.utils.multiclass import unique_labels

def plot_confusion_matrix(y_true, y_pred, classes,
                          normalize=False,
                          title=None,
                          cmap=plt.cm.Blues):
    """
    This function prints and plots the confusion matrix.
    Normalization can be applied by setting `normalize=True`.
    """
    if not title:
        if normalize:
            title = 'Normalized confusion matrix'
        else:
            title = 'Confusion matrix, without normalization'

    # Compute confusion matrix
    cm = confusion_matrix(y_true, y_pred)
    # Only use the labels that appear in the data
    classes = ["very low", "low", "medium", "high", "very high"]

    fig, ax = plt.subplots()
    im = ax.imshow(cm, interpolation='nearest', cmap=cmap)
    ax.figure.colorbar(im, ax=ax)
    # We want to show all ticks...
    ax.set(xticks=np.arange(cm.shape[1]),
           yticks=np.arange(cm.shape[0]),
           # ... and label them with the respective list entries
           xticklabels=classes, yticklabels=classes,
           title=title,
           ylabel='True label',
           xlabel='Predicted label')

    # Rotate the tick labels and set their alignment.
    plt.setp(ax.get_xticklabels(), rotation=45, ha="right",
             rotation_mode="anchor")

    # Loop over data dimensions and create text annotations.
    fmt = '.2f' if normalize else 'd'
    thresh = cm.max() / 2.
    for i in range(cm.shape[0]):
        for j in range(cm.shape[1]):
            ax.text(j, i, format(cm[i, j], fmt),
                    ha="center", va="center",
                    color="white" if cm[i, j] > thresh else "black")
    fig.tight_layout()
    return ax

In [ ]:
np.set_printoptions(precision=2)
class_names = ["very low", "low", "medium", "high", "very high"]

# Plot non-normalized confusion matrix
plot_confusion_matrix(y_test, y_pred_rf, classes=class_names,
                      title='Confusion matrix, without normalization')


In [ ]:
# Plot normalized confusion matrix
plot_confusion_matrix(y_test, y_pred_rf, classes=class_names, normalize=True,
                      title='Normalized confusion matrix')

plt.show()

### TODO modelling

1. NB and MLP
3. Ensemble
4. Add to hyperparameter tuning above to improve performance
